In [50]:
import pandas as pd
import numpy as np
import pickle
import plotly.express as px
import plotly.graph_objects as go
from copy import deepcopy
import json
import torch
import torch.nn as nn
from math import sin, cos, sqrt, atan2, radians
import copy
from sklearn.cluster import *
from sklearn.decomposition import PCA
from sklearn.metrics import silhouette_score
from sklearn_extra.cluster import KMedoids
import geopy.distance
from scipy.spatial.distance import *
import random
import numpy as np
import osmnx as ox
import networkx as nx
from sklearn.neighbors import KDTree
import folium
import matplotlib.pyplot as plt

In [51]:
import python.data as data
import python.display as dp
import python.voxels as voxel
import python.metric as metric
import python.clustering as cl
import python.RNN as RNN
#import python.learning as learning
#from python.NN import *

# Chargement des données

In [52]:
with open("files/gpx_matched_simplified.df",'rb') as infile:
    df_simplified = pickle.load(infile)
tab_routes_voxels_simplified, dict_voxels_simplified = voxel.create_dict_vox(df_simplified, df_simplified.iloc[0]["route_num"], df_simplified.iloc[-1]["route_num"])
tab_routes_voxels_simplified_global = voxel.get_tab_routes_voxels_global(dict_voxels_simplified, df_simplified.iloc[-1]["route_num"])

with open("files/gpx_pathfindind_cycling.df",'rb') as infile:
    df_pathfinding = pickle.load(infile)       
tab_routes_voxels_pathfinding, dict_voxels_pathfinding = voxel.create_dict_vox(df_pathfinding, df_pathfinding.iloc[0]["route_num"], df_pathfinding.iloc[-1]["route_num"])
tab_routes_voxels_pathfinding_global = voxel.get_tab_routes_voxels_global(dict_voxels_pathfinding, df_pathfinding.iloc[-1]["route_num"])

In [53]:
print(len(tab_routes_voxels_pathfinding))

899


## Piste cyclable

In [54]:
#df_bikepath = data.load_bikepath('datas/pvo_patrimoine_voirie.json')
with open("files/bikepath_fusioned.df", "rb") as outfile:
    df_bikepath = pickle.load(outfile)
    df_bikepath = pd.DataFrame(df_bikepath, dtype=object)
      
_, dict_voxels_bikepath = voxel.create_dict_vox(df_bikepath, df_bikepath.iloc[0]["route_num"], df_bikepath.iloc[-1]["route_num"], True)


In [55]:
def bikepath_fusion(df_bikepath):
    verbose = False

    n_route = 0
    n_route_next = n_route+1
    n = n_route
    nb_change = 0
    while(n_route < df_bikepath.iloc[-1]["route_num"]):
        p1 = df_bikepath[df_bikepath["route_num"]==n_route].values.tolist()[-1][:2]
        p2 = df_bikepath[df_bikepath["route_num"]==n_route_next].values.tolist()[0][:2]
        v1 = voxel.find_voxel_int(p1)
        v2 = voxel.find_voxel_int(p2)
        if(v1 == v2):
            tab_changes = [n_route]
            while(v1 == v2):
                tab_changes.append(n_route_next)
                n_route_next += 1
                n_route += 1
                p1 = df_bikepath[df_bikepath["route_num"]==n_route].values.tolist()[-1][:2]
                p2 = df_bikepath[df_bikepath["route_num"]==n_route_next].values.tolist()[0][:2]
                v1 = voxel.find_voxel_int(p1)
                v2 = voxel.find_voxel_int(p2)
            for i in range(len(tab_changes)):
                df_bikepath = df_bikepath.replace({"route_num": tab_changes[i]}, n)
                if(verbose):
                    print(tab_changes[i], "->", n, "equals")
                if(i != 0):
                    nb_change += 1
            n+=1
            n_route += 1
        else:
            df_bikepath = df_bikepath.replace({"route_num": n_route}, n)
            if(verbose):
                print(n_route, "->", n)
            n_route += 1
            n += 1
        n_route_next += 1
    df_bikepath = df_bikepath.replace({"route_num": df_bikepath.iloc[-1]["route_num"]}, n)
    print(nb_change, "changes")
    return df_bikepath
    
#df_bikepath_fusioned = bikepath_fusion(df_bikepath)

In [56]:
def bikepath_fusion_2(df_bikepath):
    df_bikepath_fusioned = pd.DataFrame()
    route_num_fusioned = 0
    nb_changes = 0
    for i in range(int(df_bikepath.iloc[-1]["route_num"])):
        if(len(df_bikepath[df_bikepath["route_num"]==i]) > 0):
            print(i)
            for j in range(i, int(df_bikepath.iloc[-1]["route_num"])):
                if(len(df_bikepath[df_bikepath["route_num"]==j]) > 0):
                    p1 = df_bikepath[df_bikepath["route_num"]==i].values.tolist()[-1][:2]
                    p2 = df_bikepath[df_bikepath["route_num"]==j].values.tolist()[0][:2]
                    v1 = voxel.find_voxel_int(p1)
                    v2 = voxel.find_voxel_int(p2)
                    if(v1 == v2):
                        nb_changes += 1
                        df_bikepath = df_bikepath.replace({"route_num": j}, i)
                        
            df_temp = df_bikepath[df_bikepath["route_num"]==i]
            df_temp["route_num"] = route_num_fusioned
            route_num_fusioned += 1
            df_bikepath_fusioned = df_bikepath_fusioned.append(df_temp)            
    print(nb_changes, "changes")
    return df_bikepath_fusioned
    
#df_bikepath_fusioned = bikepath_fusion_2(df_bikepath)       

## Map Matching

In [57]:
data.mapmatching("files/gpx.df", "files/gpx_matched.df", 0)

In [58]:
data.simplify_gps("files/gpx_matched.df", "files/gpx_matched_simplified.df", 0)

28508
28508


In [59]:
data.simplify_gps("files/osmnx_pathfinding.df", "files/osmnx_pathfinding_simplified.df", 0)

17763
17763


## Pathfinding

In [60]:
data.pathfinding_mapbox("files/gpx_matched_simplified.df", "files/gpx_pathfindind_cycling.df", 0)

## Distance

In [61]:
data.compute_distance("files/gpx_matched_simplified.df", "files/distances_gpx_matched.tab")
data.compute_distance("files/gpx_pathfindind_cycling.df", "files/distances_gpx_pathfinding_cycling.tab")
data.compute_distance("files/osmnx_pathfinding_simplified.df", "files/distances_gpx_osmnx.tab")

# Contrôle de l'affichage

In [62]:
display = True

# Test voxels

In [63]:
if(display):
    with open("files/gpx_matched_simplified.df",'rb') as infile:
            df_simplified = pickle.load(infile)

    nb_routes = 2
    min_routes = 2
    df_simplified["type"] = 0
    df_display = df_simplified[(df_simplified["route_num"]<=nb_routes)]

    _, dict_voxels = voxel.create_dict_vox(df_display, 1, nb_routes)
    tab_vox = voxel.get_voxels_with_min_routes(dict_voxels, min_routes)
    print(len(tab_vox)/4)

    df = pd.DataFrame(tab_vox, columns=["lat", "lon", "route_num", "type"])
    df_display = df_display.append(df)
    dp.display(df_display, color="type")    


11.0


# Heat Maps

In [64]:
if(display):     
    tab = []
    for key in dict_voxels_simplified:
        vox_str = key.split(";")
        vox_int = [int(vox_str[0]), int(vox_str[1])]
        vox_pos = voxel.get_voxel_points(vox_int, 0)
        tab.append([vox_pos[0][0], vox_pos[0][1], dict_voxels_simplified[key]["cyclability_coeff"]])

    df = pd.DataFrame(tab, columns=["lat", "lon", "Cyclability coefficient"])
    fig = px.scatter_mapbox(df, lat="lat", lon="lon",  color="Cyclability coefficient", size="Cyclability coefficient", zoom=11)
    fig.show()
    #fig.write_image("images/heatmap_simplified.png")

In [65]:
if(display):
    tab = []
    for key in dict_voxels_pathfinding:
        vox_str = key.split(";")
        vox_int = [int(vox_str[0]), int(vox_str[1])]
        vox_pos = voxel.get_voxel_points(vox_int, 0)
        tab.append([vox_pos[0][0], vox_pos[0][1], dict_voxels_pathfinding[key]["cyclability_coeff"]])

    df = pd.DataFrame(tab, columns=["lat", "lon", "Cyclability coefficient"])
    fig = px.scatter_mapbox(df, lat="lat", lon="lon",  color="Cyclability coefficient", size="Cyclability coefficient", zoom=11)
    fig.show()
    #fig.write_image("images/heatmap_mapbox.png")

In [66]:
if(display):
    tab_routes_voxels_common = []
    dict_voxels_common = {}
    tab = []

    for i in range(len(tab_routes_voxels_pathfinding_global)):
        tab_routes_voxels_common.append(list(set(tab_routes_voxels_pathfinding_global[i]).intersection(set(tab_routes_voxels_simplified_global[i]))))

    for i in range(len(tab_routes_voxels_common)):
        for key in tab_routes_voxels_common[i]:
            if key not in dict_voxels_common:
                dict_voxels_common[key] = [i]
            else:
                dict_voxels_common[key].append(i)

    for key in dict_voxels_common:
        print(key)
        tab_routes = dict_voxels_common[key]
        vox_str = key.split(";")
        vox_int = [int(vox_str[0]), int(vox_str[1])]
        vox_pos = voxel.get_voxel_points(vox_int, 0)
        if(len(tab_routes) >= 0):
            tab.append([vox_pos[0][0], vox_pos[0][1], len(tab_routes)])

    df = pd.DataFrame(tab, columns=["lat", "lon", "value"])
    #fig = px.scatter_mapbox(df, lat="lat", lon="lon",  color="value", size="value", zoom=10)
    #fig.show()


457030;49015
457595;48755
457050;49015
457045;49015
457570;48760
457580;48760
457555;48760
457575;48760
457050;49010
457040;49015
457550;48765
457035;49020
457560;48765
457590;48755
457545;48765
457590;48760
457555;48765
457590;48765
457550;48760
457580;48765
457585;48760
457575;48765
457055;49005
457040;49020
457565;48760
457045;49020
457560;48760
457035;49015
457055;49000
457585;48765
457050;49005
457245;48910
457455;48745
457440;48745
457595;48750
457510;48760
457500;48755
457605;48745
457410;48740
457525;48765
457620;48740
457260;48870
457290;48795
457630;48740
457355;48740
457605;48750
457350;48735
457415;48740
457445;48740
457330;48740
457405;48740
457430;48740
457720;48735
457380;48740
457710;48735
457280;48820
457350;48740
457245;48900
457520;48765
457345;48735
457280;48810
457475;48750
457505;48760
457620;48735
457270;48845
457645;48735
457240;48920
457245;48895
457235;48925
457385;48740
457460;48750
457245;48905
457670;48735
457435;48740
457270;48835
457260;48865
457285;48800

457630;48745
457625;48780
457625;48775
457685;48310
457685;48305
457625;48785
457625;48765
457250;48395
457200;48405
457265;48325
457265;48335
457245;48395
457235;48400
457230;48400
457210;48400
457195;48405
457265;48345
457255;48370
457240;48400
457220;48400
457215;48400
457250;48375
457255;48375
457250;48385
457260;48345
457265;48340
457265;48330
457265;48350
457225;48400
457250;48370
457205;48405
457250;48390
457250;48380
457105;48540
457130;48015
457155;47985
457125;48025
457150;47990
457125;48030
457150;47995
457135;48015
457155;47980
457130;48020
457130;48025
457150;48005
457150;48000
457145;48010
457160;47890
457155;47970
457155;47975
457165;47950
457170;47915
457165;47955
457170;47930
457175;47910
457165;47895
457170;47925
457150;47890
457160;47960
457175;47905
457160;47895
457170;47900
457165;47945
457155;47895
457160;47965
457170;47935
457170;47920
457170;47945
457155;47890
457170;47940
457155;47965
457170;47905
457165;47900
457170;47910
457160;47955
457260;48140
457155;47870

In [67]:
if(display):
    tab = []
    for key in dict_voxels_pathfinding:
        tab_routes = dict_voxels_pathfinding[key]["tab_routes_starting"]
        vox_str = key.split(";")
        vox_int = [int(vox_str[0]), int(vox_str[1])]
        vox_pos =voxel. get_voxel_points(vox_int, 0)
        if(len(tab_routes) >= 0):
            tab.append([vox_pos[0][0], vox_pos[0][1], len(tab_routes)])

    df = pd.DataFrame(tab, columns=["lat", "lon", "value"])
    fig = px.scatter_mapbox(df, lat="lat", lon="lon",  color="value", size="value", zoom=10)
    fig.show()

# Graphes distances

In [68]:
if(display):
    with open("files/distances_gpx_matched.tab",'rb') as infile:
        tab_distances = pickle.load(infile)    

    with open("files/distances_gpx_pathfinding_cycling.tab",'rb') as infile:
        tab_distances_pf = pickle.load(infile)   

    print(len(tab_distances_pf))

    fig = go.Figure()
    # Create and style traces
    fig.add_trace(go.Scatter(y=tab_distances, name='Distance réel',
                             line=dict(color='firebrick', width=4)))
    fig.add_trace(go.Scatter(y=tab_distances_pf, name = 'Distance plus court chemin',
                             line=dict(color='royalblue', width=4)))

    # Here we modify the tickangle of the xaxis, resulting in rotated labels.
    fig.update_layout(barmode='group', xaxis_tickangle=-45)
    fig.show()
    #fig.write_image("images/graph_distance.png")

900


In [69]:
if(display):

    tab_distances_relatives = []
    for i in range(len(tab_distances)):
        tab_distances_relatives.append(tab_distances[i]-tab_distances_pf[i])

    fig = go.Figure()
    # Create and style traces
    fig.add_trace(go.Scatter(y=tab_distances_relatives, name='Distance réel',
                             line=dict(width=4)))

    # Here we modify the tickangle of the xaxis, resulting in rotated labels.
    fig.update_layout(barmode='group', xaxis_tickangle=-45)
    fig.show()
    #fig.write_image("images/graph_diff_distance.png")

# CDF

In [70]:
if(display):
    tab_distances_relatives.sort()
    tab_display = []
    tab_axis = []
    dist_max = 0
    nb_routes = 0
    for dist in tab_distances_relatives:
        if(dist > dist_max):
            tab_display.append(nb_routes/len(tab_distances_relatives))
            tab_axis.append(dist_max)
            dist_max += 0.2
        nb_routes += 1
    fig = go.Figure()
    # Create and style traces
    fig.add_trace(go.Scatter(y=tab_display, x=tab_axis, name='Distance réel',
                             line=dict(width=4)))


    # Here we modify the tickangle of the xaxis, resulting in rotated labels.
    fig.update_layout(barmode='group', xaxis_tickangle=-45)
    fig.show()
    #fig.write_image("images/cdf.png")

# Metrique chemin-chemin

In [71]:
#tab = np.array(metric.tab_dist)
#print(tab.mean())

In [72]:
m = metric.GPSDistanceTuto()
threshold = 2

m = metric.GPSDistanceCustom()
threshold = 200
#neuro_cluster("gpx_matched_simplified.df", "cluster_custom.tab", metric, threshold)

In [73]:
if(display):
    index_cluster = 0

    with open('files/cluster_custom.tab', 'rb') as infile:
        clusters = pickle.load(infile)   
    with open('files/cluster_tuto.tab', 'rb') as infile:
        clusters = pickle.load(infile)

    df_display = pd.DataFrame(columns=['lat', 'lon', 'route_num'])
    i = 0
    print(len(clusters[index_cluster]))
    for route in clusters[index_cluster]:
        df_temp = pd.DataFrame(route, columns=['lat', 'lon'])
        df_temp["route_num"] = i
        df_display = df_display.append(df_temp)
        i+=1
    dp.display(df_display)

22


# Matrice de distance

In [74]:
new_matrix = True

In [75]:
if(new_matrix):
    
    distance_matrix = np.empty([df_simplified.iloc[-1]["route_num"], df_simplified.iloc[-1]["route_num"]])

    pca = PCA(n_components=1)

    for i in range(df_simplified.iloc[-1]["route_num"]):
        #print(i)
        for j in range(i, df_simplified.iloc[-1]["route_num"]):
            coeff = metric.get_distance_voxels(i+1, j+1, tab_routes_voxels_simplified_global)
            #coeff = metric.get_distance_euclidian(df_cluster[df_cluster["route_num"]==i+1], df_cluster[df_cluster["route_num"]==j+1], pca)
            #coeff = metric.get_distance_hausdorff(df_cluster[df_cluster["route_num"]==i+1], df_cluster[df_cluster["route_num"]==j+1])
            distance_matrix[i][j] = coeff[0]
            distance_matrix[j][i] = coeff[1]

    print("number of non-zero in diag : ", len(np.nonzero(np.diagonal(distance_matrix))[0]))

number of non-zero in diag :  0


In [76]:
num_vox = 0
tab_vox = []
df_display = df_simplified[df_simplified["route_num"]==1]
df_display["type"] = 0
for v in tab_routes_voxels_simplified[0]:
    vox_str = v.split(";")
    vox_int = [int(vox_str[0]), int(vox_str[1])]
    tab_vox += voxel.get_voxel_points(vox_int, num_vox)
    num_vox -= 1
    
df = pd.DataFrame(tab_vox, columns=["lat", "lon", "route_num", "type"])
df_display = df_display.append(df)
dp.display(df_display, color="type")   

/home/lucas/.local/share/virtualenvs/bikesharing-PfOBh4Im/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



# Graphes clustering

In [77]:
start_variable = 0.1
stop_variable = 0.9
step_variable = 0.1

tab_nb_clusters = []
tab_noise = []
tab_nb_mini_clusters = []
tab_nb_big_clusters = []
tab_mean = []
tab_silhouette = []

for variable in np.arange(start_variable, stop_variable, step_variable):
    c = DBSCAN(eps=variable, min_samples=5, metric='precomputed')
    clusters = cl.cluster(distance_matrix, c)
    dict_cluster = cl.tab_clusters_to_dict(clusters)
    silhouette = silhouette_score(distance_matrix, clusters, metric="precomputed")

    nb_mini_clusters= 0
    nb_big_clusters = 0
    mean = 0
    for i in range(len(dict_cluster)-1):
        if(len(dict_cluster[i]) > 15):
            nb_big_clusters += 1
        elif(len(dict_cluster[i]) == 1):
            nb_mini_clusters += 1
        mean+=len(dict_cluster[i])
        
    tab_nb_clusters.append(len(dict_cluster)-1)
    tab_noise.append(clusters.tolist().count(-1))
    tab_nb_mini_clusters.append(nb_mini_clusters)
    tab_nb_big_clusters.append(nb_big_clusters)
    tab_mean.append(mean/(len(dict_cluster)-1))
    tab_silhouette.append(silhouette)
    


In [78]:
fig = go.Figure()
    
fig.add_trace(go.Scatter(x=np.arange(start_variable, stop_variable, step_variable), 
                         y=tab_nb_mini_clusters, name='Mini clusters',
                         line=dict(color='firebrick', width=4)))
fig.add_trace(go.Scatter(x=np.arange(start_variable, stop_variable, step_variable), 
                         y=tab_nb_big_clusters, name = 'Big clusters',
                         line=dict(color='royalblue', width=4)))


fig.add_shape(type="line", x0=0, y0=11, x1=0.4, y1=11,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))
fig.add_shape(type="line", x0=0.4, y0=0, x1=0.4, y1=11,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))

fig.add_shape(type="line", x0=0.4, y0=11, x1=0.4, y1=15,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))
fig.add_shape(type="line", x0=0, y0=15, x1=0.4, y1=15,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))

# Here we modify the tickangle of the xaxis, resulting in rotated labels.
fig.update_layout(barmode='group', xaxis_tickangle=-45)
fig.show()
#fig.write_image("images/clusters_dbscan.png")

In [79]:
fig = go.Figure()
    
fig.add_trace(go.Scatter(x=np.arange(start_variable, stop_variable, step_variable), 
                         y=tab_nb_clusters, name='Mean size',
                         line=dict(color='firebrick', width=4)))

fig.add_shape(type="line", x0=0, y0=74, x1=0.4, y1=74,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))
fig.add_shape(type="line", x0=0.4, y0=0, x1=0.4, y1=74,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))


# Here we modify the tickangle of the xaxis, resulting in rotated labels.
fig.update_layout(barmode='group', xaxis_tickangle=-45)
fig.show()
#fig.write_image("images/mean_dbscan.png")

In [80]:
fig = go.Figure()
    
fig.add_trace(go.Scatter(x=np.arange(start_variable, stop_variable, step_variable), 
                         y=tab_silhouette, name='Silhouette',
                         line=dict(color='royalblue', width=4)))

fig.add_shape(type="line", x0=0, y0=0.3898887, x1=0.4, y1=0.3898887,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))
fig.add_shape(type="line", x0=0.4, y0=0, x1=0.4, y1=0.3898887,
            line=dict(color="LightSeaGreen", width=4, dash="dot"))


# Here we modify the tickangle of the xaxis, resulting in rotated labels.
fig.update_layout(barmode='group', xaxis_tickangle=-45)
fig.show()
#fig.write_image("images/silhouette_dbscan.png")

# Affichage/Propriétés des clusters

In [81]:
def cluster_properties(dict_cl, X, cl, metric=None):
    mean = 0
    mini_clusters = []
    big_clusters = []
    for i in dict_cl:
        if(i != -1):
            if(len(dict_cl[i]) > len(X)/60):
                big_clusters.append(i)
            elif(len(dict_cl[i]) <= len(X)/500):
                mini_clusters.append(i)
            mean+=len(dict_cl[i])

    if(metric != None):
        silhouette = silhouette_score(X, cl, metric=metric)
    else:
        silhouette = silhouette_score(X, cl)

    print(len(big_clusters), "big clusters:", big_clusters)
    print(len(mini_clusters), "mini clusters :", mini_clusters)
    print()
    print("mean size :", mean/(len(dict_cl)-1))
    print()
    print("silhouette score :", silhouette)

# Clustering

In [82]:
if(new_matrix):
    pca = PCA(n_components=750)
    #distance_matrix_reduced = pca.fit_transform(distance_matrix)

    dbscan = DBSCAN(eps=0.4, min_samples=5, metric='precomputed')
    optics = OPTICS(min_samples=10, metric='precomputed')
    kmedoids = KMedoids(n_clusters=75, metric=metric.get_distance_voxels_symetric, random_state=0)
    
    clustering = dbscan
    X = distance_matrix
    if(clustering == kmedoids):
        X = np.asarray(np.expand_dims(np.arange(1, 900, 1), axis=1))

    clusters = cl.cluster(X, clustering)
    dict_cluster = cl.tab_clusters_to_dict(clusters)

    print(len(dict_cluster)-1, "clusters")
    print("noise:", clusters.tolist().count(-1))
    print()
    cluster_properties(dict_cluster, distance_matrix, clusters, "precomputed")

74 clusters
noise: 81

16 big clusters: [0, 1, 4, 46, 18, 30, 12, 16, 19, 24, 45, 29, 33, 35, 36, 62]
11 mini clusters : [2, 5, 6, 38, 48, 53, 55, 56, 60, 64, 71]

mean size : 11.054054054054054

silhouette score : 0.38988872319145457


In [83]:
nb_cluster = 16
print(len(dict_cluster[nb_cluster]))
#dp.display_routes(df_cluster, dict_cluster[nb_cluster])
dp.display_cluster_heatmap(df_simplified, dict_cluster[nb_cluster])

95


/home/lucas/bikesharing/python/display.py:47: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



# Voxel Clustering

In [84]:
clusters_used = []
for key in dict_voxels_bikepath:
    if key in dict_voxels_pathfinding:
        if(dict_voxels_bikepath[key]["cluster"] not in clusters_used):
            dict_voxels_pathfinding[key]["cluster"] = len(clusters_used)
            clusters_used.append(dict_voxels_bikepath[key]["cluster"])
        else:
            dict_voxels_pathfinding[key]["cluster"] = clusters_used.index(dict_voxels_bikepath[key]["cluster"])

In [85]:
X = []
for key in dict_voxels_pathfinding:
    if("cluster" not in dict_voxels_pathfinding[key]):
        vox_str = key.split(";")
        vox_int = [int(vox_str[0]), int(vox_str[1])]
        tab_points = voxel.get_voxel_points(vox_int)
        X.append([tab_points[0][0], tab_points[0][1], dict_voxels_pathfinding[key]["cyclability_coeff"]])
print(len(X))

5096


In [86]:
kmeans = KMeans(n_clusters=len(X)//10, random_state=0)
dbscan = DBSCAN(eps=0.5, min_samples=5)
clusters = cl.cluster(X, kmeans)
dict_cluster_voxel = cl.tab_clusters_to_dict(clusters)

print(len(dict_cluster_voxel)-1, "clusters")
print("noise:", clusters.tolist().count(-1))
print()
cluster_properties(dict_cluster_voxel, X, clusters)


508 clusters
noise: 0

0 big clusters: []
313 mini clusters : [215, 445, 398, 442, 330, 456, 491, 21, 188, 231, 488, 180, 193, 361, 141, 477, 296, 113, 425, 328, 489, 24, 331, 413, 186, 291, 252, 437, 385, 150, 145, 176, 42, 247, 122, 277, 268, 222, 116, 389, 177, 373, 64, 110, 60, 409, 185, 431, 382, 303, 339, 356, 221, 63, 179, 433, 159, 85, 97, 326, 77, 263, 470, 467, 136, 121, 279, 259, 393, 175, 416, 333, 34, 376, 372, 156, 25, 240, 478, 440, 415, 45, 289, 435, 381, 153, 432, 61, 316, 424, 502, 127, 484, 13, 201, 506, 444, 337, 307, 140, 203, 447, 342, 56, 284, 243, 399, 272, 401, 480, 386, 357, 370, 133, 189, 237, 66, 293, 40, 184, 29, 395, 417, 0, 430, 414, 410, 443, 254, 388, 405, 503, 223, 190, 147, 497, 32, 100, 264, 109, 118, 334, 457, 4, 397, 426, 378, 368, 348, 319, 18, 325, 192, 466, 318, 256, 44, 408, 216, 251, 212, 117, 501, 452, 394, 208, 346, 306, 2, 364, 283, 142, 327, 402, 287, 476, 162, 292, 218, 464, 5, 422, 214, 353, 434, 82, 451, 206, 202, 384, 17, 454, 458, 349

In [87]:
save_kmeans = False

if(save_kmeans):
    with open("files/kmeans.sk",'wb') as outfile:
        pickle.dump(kmeans, outfile)

In [88]:
num_cluster = 5

tab = []
for vox in dict_cluster_voxel[num_cluster]:
    tab.append(X[vox])

df = pd.DataFrame(tab, columns=["lon", "lat", "value"])
fig = px.scatter_mapbox(df, lat="lat", lon="lon",  color="value", size="value", zoom=10)
fig.show()
    

In [89]:
save = False


dict_voxels_pathfinding_tosave = deepcopy(dict_voxels_pathfinding)
for c in dict_cluster_voxel:
    for vox in dict_cluster_voxel[c]:
        v = X[vox]
        vox_int = voxel.find_voxel_int([v[0], v[1]])
        key = str(vox_int[0])+";"+str(vox_int[1])
        dict_voxels_pathfinding_tosave[key]["cluster"] = len(clusters_used)+c
if(save == True):
    with open("./files/voxels_pathfinding.dict",'wb') as outfile:
        pickle.dump(dict_voxels_pathfinding_tosave, outfile)

# Osmnx

In [90]:
def generate_graphs():
    # creating a graph by using a point
    lyon = (45.74846, 4.84671)
    st_etienne = (45.4333, 4.4)
    G_lyon = ox.graph_from_point(lyon, distance=7500)
    G_stetienne = ox.graph_from_point(st_etienne, distance=7500)
    G = G_lyon
    # quick plot
    #ox.plot_graph(G, fig_height=20, fig_width=20, edge_color='black')
    return G_lyon, G_stetienne
#G_lyon, G_stetienne = generate_graphs()

In [91]:
with open("files/lyon.ox", "rb") as infile:
    G_lyon = pickle.load(infile)
with open("files/st_etienne.ox", "rb") as infile:
    G_stetienne = pickle.load(infile)
    
nodes_lyon, _ = ox.graph_to_gdfs(G_lyon)
tree_lyon = KDTree(nodes_lyon[['y', 'x']], metric='euclidean')

nodes_stetienne, _ = ox.graph_to_gdfs(G_stetienne)
tree_stetienne = KDTree(nodes_stetienne[['y', 'x']], metric='euclidean')

G = G_lyon
tree = tree_lyon

In [92]:
df_temp = df_simplified[df_simplified["route_num"]==i+1]
d_point = [df_temp.iloc[0]["lat"], df_temp.iloc[0]["lon"]]
f_point = [df_temp.iloc[-1]["lat"], df_temp.iloc[-1]["lon"]]

In [93]:

route = data.pathfind_route_osmnx(d_point, f_point, tree, G, i)
ox.plot_route_folium(G, route, route_color='green')

In [94]:
with open("files/osmnx_pathfinding.df", "rb") as infile:
    df_pathfinding_osmnx = pickle.load(infile)

for i in range(df_pathfinding_osmnx.iloc[-1]["route_num"], df_simplified.iloc[-1]["route_num"]):
    df_temp = df_simplified[df_simplified["route_num"]==i+1]
    d_point = [df_temp.iloc[0]["lat"], df_temp.iloc[0]["lon"]]
    f_point = [df_temp.iloc[-1]["lat"], df_temp.iloc[-1]["lon"]]
    if(d_point[0] < 45.5):
        tree = tree_stetienne
        G = G_stetienne
    else:
        tree = tree_lyon
        G = G_lyon
    route = data.pathfind_route_osmnx(d_point, f_point, tree, G, i)
    route_coord = [[G.nodes[x]["y"], G.nodes[x]["x"]] for x in route]
    route_coord = [x + [i+1] for x in route_coord]
    df_pathfinding_osmnx = df_pathfinding_osmnx.append(pd.DataFrame(route_coord, columns=["lat", "lon", "route_num"]))
    

# Validation

In [95]:
import python.validation as validation

with open("files/cluster_dbscan_custom.tab",'rb') as infile:
    tab_clusters = pickle.load(infile)
with open("files/voxels_pathfinding.dict",'rb') as infile:
    dict_voxels = pickle.load(infile)
with open("files/kmeans.sk",'rb') as infile:
    kmeans = pickle.load(infile)
    
df = df_pathfinding
    
size_data = 1
hidden_size = 256
num_layers = 2
voxels_frequency = 4

network = RNN.RNN_LSTM(size_data, max(tab_clusters)+1, hidden_size, num_layers)
network.load_state_dict(torch.load("files/network_osmnx.pt"))
network.eval()

nb_good_predict = 0
nb_predict = 0

deviation = 0 #5e-3

tab_predict = []

i=675

for i in range(9, 10): #len(tab_clusters)):
    print(i)
    if(tab_clusters[i] != -1 and i != 675):
        df_temp = df[df["route_num"]==i+1]
        d_point = [df_temp.iloc[0]["lat"], df_temp.iloc[0]["lon"]]
        f_point = [df_temp.iloc[-1]["lat"], df_temp.iloc[-1]["lon"]]
        rand = random.uniform(-deviation, deviation)
        d_point[0] += rand
        rand = random.uniform(-deviation, deviation)
        d_point[1] += rand
        rand = random.uniform(-deviation, deviation)
        f_point[0] += rand
        rand = random.uniform(-deviation, deviation)
        f_point[1] += rand
        
        if(d_point[0] < 45.5):
            tree = tree_stetienne
            G = G_stetienne
        else:
            tree = tree_lyon
            G = G_lyon
        df_route, cl, nb_new_cluster = validation.find_cluster(d_point, f_point, network, voxels_frequency, df_pathfinding, dict_voxels, 
                                     kmeans, tree, G, False)
        if(cl == tab_clusters[i]):
            nb_good_predict += 1
        nb_predict += 1
if(nb_predict > 0):
    tab_predict.append(nb_good_predict/nb_predict)

tot_predict = 0
for predict in tab_predict:
    tot_predict += predict
print(tot_predict/len(tab_predict))


9
1.0


In [96]:
dp.display(df_route)

In [97]:
dp.display_cluster_heatmap(df_simplified, dict_cluster[cl])

/home/lucas/bikesharing/python/display.py:47: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [98]:
dp.display(df_simplified[df_simplified["route_num"]==i+1])

In [99]:
df_simplified

lat      lon route_num  type
0   45.7598  4.87564         1     0
1   45.7595  4.87557         1     0
2   45.7594  4.87589         1     0
3   45.7583  4.87658         1     0
4   45.7561  4.87612         1     0
..      ...      ...       ...   ...
61  45.7785  4.80798       899     0
62  45.7805  4.80921       899     0
63  45.7806  4.80916       899     0
64  45.7827  4.81093       899     0
65  45.7831  4.80931       899     0

[28508 rows x 4 columns]